In [1]:
import pandas as pd

pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

In [2]:
from google.colab import drive

drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
wefarm = pd.read_parquet("/content/drive/MyDrive/DataKit_WeFarm/wefarm.parquet")

In [4]:
wefarm["response_sent_dt"] = pd.to_datetime(wefarm["response_sent"], format="ISO8601")
wefarm["question_set_dt"] = pd.to_datetime(wefarm["question_sent"], format="ISO8601")

In [5]:

def parse_datetime_col(df, colstr):
  df[f'{colstr}_year'] = df[colstr].dt.year
  df[f'{colstr}_month'] = df[colstr].dt.month
  df[f'{colstr}_day'] = df[colstr].dt.day
  df[f'{colstr}_hour'] = df[colstr].dt.hour
  df[f'{colstr}_minute'] = df[colstr].dt.minute
  df[f'{colstr}_second'] = df[colstr].dt.second
  df[f'{colstr}_day_name'] = df[colstr].dt.day_name()
  df[f'{colstr}_day_of_week'] = df[colstr].dt.day_of_week
  df[f'{colstr}_month_name'] = df[colstr].dt.month_name()
  df[f'{colstr}_quarter'] = df[colstr].dt.quarter
  df[f'{colstr}_week'] = df[colstr].dt.isocalendar().week
  df[f'{colstr}_date'] = df[colstr].dt.date
  df[f'{colstr}_time'] = df[colstr].dt.time

  return df

In [6]:
wefarm = parse_datetime_col(wefarm, "response_sent_dt")
wefarm = parse_datetime_col(wefarm, "question_set_dt")

In [7]:
niche = pd.read_parquet("/content/drive/MyDrive/DataKit_WeFarm/en_questions_cat_niche.parquet")
broad = pd.read_parquet("/content/drive/MyDrive/DataKit_WeFarm/en_questions_cat_broad.parquet")

In [8]:
all = pd.merge(wefarm, niche, on="question_id").merge(
  broad, on="question_id"
)

In [9]:
import json

with open("/content/drive/MyDrive/DataKit_WeFarm/segment_user_ids.json", "r") as r:
    segment_user_id_dct = json.load(r)

In [10]:
segment_user_id_dct.keys()

dict_keys(['user_activity_post_count', 'speed_post_response', 'unique_askers', 'tenure'])

In [11]:
# segment_user_id_dct["user_activity_post_count"].keys()

In [12]:
from collections import defaultdict

user_segments = defaultdict(dict)
for agg, dct in segment_user_id_dct.items():
  for segment, user_ids in dct.items():
    for user_id in user_ids:
      user_segments[user_id][agg] = segment

row_lst = []
for user_id, segments in user_segments.items():
  row = {"user_id": user_id}
  row.update(segments)
  row_lst.append(row)

user_segments_df = pd.DataFrame(row_lst)

In [13]:
all1 = all.merge(user_segments_df, left_on="question_user_id", right_on="user_id", how="inner")

In [14]:
all2 = all1[all1["question_user_country_code"].isin(["ug", "ke"])]

In [15]:
all3 = all2.drop_duplicates("question_id")

In [16]:
all3["question_user_country_code"] = [j.upper() for j in all3["question_user_country_code"]]

/tmp/ipython-input-4026003717.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  all3["question_user_country_code"] = [j.upper() for j in all3["question_user_country_code"]]


# define topics lists

In [17]:
all3.iloc[:5, 54:173]

financial-inclusion_price  financial-inclusion_sell  \
0                        1.0                       1.0   
1                        NaN                       NaN   
2                        NaN                       NaN   
4                        1.0                       1.0   
8                        NaN                       NaN   

   financial-inclusion_buy  diversification_obtain  diversification_acquire  \
0                      1.0                     1.0                      1.0   
1                      NaN                     NaN                      NaN   
2                      NaN                     NaN                      NaN   
4                      NaN                     NaN                      NaN   
8                      NaN                     NaN                      NaN   

   question_what  question_when  question_how  question_which  crop_harvest  \
0            1.0            1.0           1.0             1.0           NaN   
1            NaN            1.0           NaN             1.0           1.0   
2            1.0            NaN           NaN             NaN           1.0   
4            1.0            1.0           1.0             1.0           NaN   
8            1.0            1.0           NaN             1.0           1.0   

   climate_time  disease_harvest  livestock_livestock  livestock_animals  \
0           NaN              NaN                  NaN                NaN   
1           1.0              1.0                  1.0                1.0   
2           NaN              1.0                  NaN                NaN   
4           1.0              NaN                  NaN                NaN   
8           NaN              1.0                  1.0                1.0   

   livestock_sheep  livestock_cattle  livestock_donkey  livestock_pig  \
0              NaN               NaN               NaN            NaN   
1              1.0               1.0               1.0            1.0   
2              NaN               NaN               NaN            NaN   
4              NaN               NaN               NaN            NaN   
8              1.0               1.0               1.0            1.0   

   livestock_cow  livestock_goat  livestock_camel  livestock_hen  \
0            NaN             NaN              NaN            NaN   
1            1.0             1.0              1.0            1.0   
2            NaN             NaN              NaN            NaN   
4            NaN             NaN              NaN            NaN   
8            1.0             1.0              NaN            NaN   

   livestock_chicken  livestock_poultry  livestock_bee  \
0                NaN                NaN            NaN   
1                1.0                1.0            1.0   
2                NaN                NaN            NaN   
4                NaN                NaN            NaN   
8                NaN                NaN            NaN   

   diversification_expand  diversification_begin  crop_plant  crop_variety  \
0                     NaN                    NaN         NaN           NaN   
1                     NaN                    NaN         NaN           NaN   
2                     NaN                    NaN         NaN           NaN   
4                     NaN                    NaN         1.0           NaN   
8                     NaN                    NaN         NaN           NaN   

   disease_plant  crop_seed  crop_grow  crop_mulch  diversification_grow  \
0            NaN        NaN        NaN         NaN                   NaN   
1            NaN        NaN        NaN         NaN                   NaN   
2            NaN        1.0        1.0         1.0                   1.0   
4            1.0        NaN        NaN         NaN                   NaN   
8            NaN        1.0        1.0         1.0                   1.0   

   crop_crop  crop_potatoes  crop_passion  crop_maize  crop_banana  \
0        NaN            NaN           NaN         NaN 

In [18]:
niche_collst = all3.columns[54:173]

In [19]:
all3.iloc[:5, -12:-5]

financial-inclusion  diversification  question  crop  climate  disease  \
0                  1.0              1.0       1.0   NaN      NaN      NaN   
1                  NaN              NaN       1.0   1.0      1.0      1.0   
2                  NaN              1.0       1.0   1.0      NaN      1.0   
4                  1.0              1.0       1.0   1.0      1.0      1.0   
8                  NaN              1.0       1.0   1.0      NaN      1.0   

   livestock  
0        NaN  
1        1.0  
2        NaN  
4        NaN  
8        1.0

In [20]:
broad_collst = all3.columns[-12:-5]

#colors

In [21]:
import plotly.express as px

segment1_color = "#A1A1A1"
segment2_color = "#F9C926"
segment3_color = "#DC7326"
segment4_color = "#4897CD"
segment5_color = "#2E9999"

In [22]:
segment_colors_dct = {
  "1": segment1_color,
  "2": segment2_color,
  "3": segment3_color,
  "4": segment4_color,
  "5": segment5_color
}

# map and pie

In [23]:
vc_country = all3["question_user_country_code"].value_counts()

# segments distribution tab

In [24]:
segmentation_collst = list(segment_user_id_dct.keys())

gb_segments_dct = {}
for segmentation in segmentation_collst:
  gb_segments_dct[segmentation] = all3.groupby([
    "question_user_country_code",
    segmentation
  ]).size().reset_index(name="n")

# topic sums

In [25]:
import numpy as np

gb_country_segment_b_topic_dct = {}
for segmentation in segmentation_collst:
  gb_sum = all3.groupby([
    "question_user_country_code",
    segmentation
  ])[broad_collst].sum()
  gb_count = all3.groupby([
    "question_user_country_code",
    segmentation
  ]).size()
  row_sums = gb_sum[broad_collst].sum(axis=1)
  gb_pct = gb_sum[broad_collst].div(row_sums, axis=0)
  gb_se = np.sqrt(gb_pct * ( 1- gb_pct)).div(np.sqrt(gb_count), axis=0)

  gb_pct = gb_pct.reset_index()
  gb_se = gb_se.reset_index()
  gb_sum = gb_sum.reset_index()

  gb_sum["count"] = gb_count.values

  gb_pct_long = gb_pct.melt(
    id_vars=["question_user_country_code", segmentation],
    value_vars=broad_collst,
    var_name="category",
    value_name="pct"
  )

  gb_se_long = gb_se.melt(
    id_vars=["question_user_country_code", segmentation],
    value_vars=broad_collst,
    var_name="category",
    value_name="se"
  )

  gb_long = gb_pct_long.merge(
    gb_se_long,
    on=["question_user_country_code", segmentation, "category"]
  ).merge(
    gb_sum[["question_user_country_code", segmentation, "count"]],
    on=["question_user_country_code", segmentation]
  ).sort_values(
    by="category"
  )

  gb_long["segment_color"] = gb_long[segmentation].map(segment_colors_dct)

  gb_country_segment_b_topic_dct[segmentation] = gb_long


In [26]:
gb_country_segment_b_topic_dct["user_activity_post_count"]

question_user_country_code user_activity_post_count             category  \
41                         KE                        2              climate   
48                         UG                        4              climate   
47                         UG                        3              climate   
46                         UG                        2              climate   
40                         KE                        1              climate   
45                         UG                        1              climate   
44                         KE                        5              climate   
43                         KE                        4              climate   
42                         KE                        3              climate   
49                         UG                        5              climate   
34                         KE                        5                 crop   
31                         KE                        2                 crop   
32                         KE                        3                 crop   
33                         KE                        4                 crop   
35                         UG                        1                 crop   
36                         UG                        2                 crop   
37                         UG                        3                 crop   
30                         KE                        1                 crop   
38                         UG                        4                 crop   
39                         UG                        5                 crop   
50                         KE                        1              disease   
59                         UG                        5              disease   
58                         UG                        4              disease   
57                         UG                        3              disease   
56                         UG                        2              disease   
55                         UG                        1              disease   
54                         KE                        5              disease   
53                         KE                        4              disease   
52                         KE                        3              disease   
51                         KE                        2              disease   
10                         KE                        1      diversification   
11                         KE                        2      diversification   
12                         KE                        3      diversification   
13                         KE                        4      diversification   
14                         KE                        5      diversification   
15                         UG                        1      diversification   
16                         UG                        2      diversification   
17                         UG                        3      diversification   
18                         UG                        4      diversification   
19                         UG                        5      diversification   
0                          KE                        1  financial-inclusion   
5                          UG                        1  financial-inclusion   
2                          KE                        3  financial-inclusion   
6                          UG                        2  financial-inclusion   
7                          UG                        3  financial-inclusion   
8                          UG                        4  financial-inclusion   
9                          UG                        5  financial-inclusion   
1                          KE                        2  financial-inclusion   
4                          KE                        5  financial-inclusion   
3                          KE                        

In [27]:
gb_country_segment_n_topic_dct = {}
for segmentation in segmentation_collst:
  gb_sum = all3.groupby([
    "question_user_country_code",
    segmentation
  ])[niche_collst].sum()
  gb_count = all3.groupby([
    "question_user_country_code",
    segmentation
  ]).size()

  row_sums = gb_sum[niche_collst].sum(axis=1)
  gb_pct = gb_sum[niche_collst].div(row_sums, axis=0)
  gb_se = np.sqrt(gb_pct * (1 - gb_pct)).div(np.sqrt(gb_count), axis=0)

  gb_pct = gb_pct.reset_index()
  gb_se = gb_se.reset_index()
  gb_sum = gb_sum.reset_index()

  gb_sum['count'] = gb_count.values

  gb_pct_long = gb_pct.melt(
    id_vars=["question_user_country_code", segmentation],
    value_vars=niche_collst,
    var_name="category",
    value_name="pct"
  )

  gb_se_long = gb_se.melt(
    id_vars=["question_user_country_code", segmentation],
    value_vars=niche_collst,
    var_name="category",
    value_name="se"
  )

  gb_long = gb_pct_long.merge(
    gb_se_long,
    on=["question_user_country_code", segmentation, "category"]
  ).merge(
    gb_sum[["question_user_country_code", segmentation, "count"]],
    on=["question_user_country_code", segmentation]
  )

  gb_long["broad_type"] = gb_long["category"].str.split("_").str[0]
  gb_long["niche"] = gb_long["category"].str.split("_").str[1]

  gb_long = gb_long.sort_values(
      by=["broad_type", "pct", "niche"],
      ascending=[True, False, True]
  )

  gb_long["segment_color"] = gb_long[segmentation].map(segment_colors_dct)

  gb_country_segment_n_topic_dct[segmentation] = gb_long

In [28]:
gb_country_segment_n_topic_dct["user_activity_post_count"]

question_user_country_code user_activity_post_count  \
102                          KE                        3   
101                          KE                        2   
103                          KE                        4   
100                          KE                        1   
107                          UG                        3   
106                          UG                        2   
104                          KE                        5   
105                          UG                        1   
108                          UG                        4   
109                          UG                        5   
873                          KE                        4   
872                          KE                        3   
874                          KE                        5   
871                          KE                        2   
870                          KE                        1   
986                          UG                        2   
988                          UG                        4   
987                          UG                        3   
985                          UG                        1   
974                          KE                        5   
445                          UG                        1   
446                          UG                        2   
447                          UG                        3   
989                          UG                        5   
448                          UG                        4   
982                          KE                        3   
973                          KE                        4   
983                          KE                        4   
981                          KE                        2   
980                          KE                        1   
984                          KE                        5   
449                          UG                        5   
442                          KE                        3   
972                          KE                        3   
440                          KE                        1   
441                          KE                        2   
711                          KE                        2   
712                          KE                        3   
443                          KE                        4   
710                          KE                        1   
971                          KE                        2   
713                          KE                        4   
878                          UG                        4   
879                          UG                        5   
970                          KE                        1   
877                          UG                        3   
444                          KE                        5   
714                          KE                        5   
717                          UG                        3   
716                          UG                        2   
718                          UG                        4   
715                          UG                        1   
876                          UG                        2   
1055                         UG                        1   
1056                         UG                        2   
734                          KE                        5   
733                          KE                        4   
732                          KE                        3   
1058                         UG                        4   
1057                         UG                        3   
875                          UG                        1   
719                          UG                        5   
731                          KE                        2   
730                          KE                        1   
1059                         UG                        5   
736                          UG              

In [29]:
# gb_country_segment_n_topic_dct = {}
# for segmentation in segmentation_collst:
#   gb = all3.groupby([
#     "question_user_country_code",
#     segmentation
#   ])[niche_collst].sum().reset_index()

#   row_sums = gb[niche_collst].sum(axis=1)
#   gb[niche_collst] = gb[niche_collst].div(row_sums, axis=0)

#   gb_long = gb.melt(
#     id_vars=["question_user_country_code", segmentation],
#     value_vars=gb.columns[2:],
#     var_name="category",
#     value_name="pct"
#   )

#   gb_long["broad_type"] = gb_long["category"].str.split("_").str[0]
#   gb_long["niche"] = gb_long["category"].str.split("_").str[1]

#   gb_long = gb_long.sort_values(
#     by=["broad_type", "pct", "niche"],
#     ascending=[True, False, True]
#   )

#   gb_long["segment_color"] = gb_long[segmentation].map(segment_colors_dct)

#   gb_country_segment_n_topic_dct[segmentation] = gb_long


#time slices

In [30]:
time_collst = [
  "question_set_dt_year",
  "question_set_dt_month",
  "question_set_dt_hour",
  "question_set_dt_day_of_week"
]

In [40]:
gb_country_segment_b_topic_time_dct = defaultdict(dict)
for segmentation in segmentation_collst:
  for time in time_collst:
    gb_sum = all3.groupby([
      "question_user_country_code",
      segmentation,
      time
    ])[broad_collst].sum()

    gb_count = all3.groupby([
      "question_user_country_code",
      segmentation,
      time
    ]).size()

    row_sums = gb_sum[broad_collst].sum(axis=1)
    gb_pct = gb_sum[broad_collst].div(row_sums, axis=0)
    gb_se = np.sqrt(gb_pct * (1 - gb_pct)).div(np.sqrt(gb_count), axis=0)

    gb_pct = gb_pct.reset_index()
    gb_se = gb_se.reset_index()
    gb_sum = gb_sum.reset_index()
    gb_sum['count'] = gb_count.values

    gb_pct_long = gb_pct.melt(
      id_vars=["question_user_country_code", segmentation, time],
      value_vars=broad_collst,
      var_name="category",
      value_name="pct"
    )

    gb_se_long = gb_se.melt(
      id_vars=["question_user_country_code", segmentation, time],
      value_vars=broad_collst,
      var_name="category",
      value_name="se"
    )

    gb_long = gb_pct_long.merge(
      gb_se_long,
      on=["question_user_country_code", segmentation, time, "category"]
    ).merge(
      gb_sum[["question_user_country_code", segmentation, time, "count"]],
      on=["question_user_country_code", segmentation, time]
    ).sort_values(
      by=time,
      ascending=False
    )

    gb_long["segment_color"] = gb_long[segmentation].map(segment_colors_dct)

    gb_country_segment_b_topic_time_dct[segmentation][time] = gb_long

In [32]:
# gb_country_segment_b_topic_time_dct = defaultdict(dict)
# for segmentation in segmentation_collst:
#   for time in time_collst:
#     gb = all3.groupby([
#       "question_user_country_code",
#       segmentation,
#       time
#     ])[broad_collst].sum().reset_index()

#     row_sums = gb[broad_collst].sum(axis=1)
#     gb[broad_collst ] = gb[broad_collst].div(row_sums, axis=0)

#     gb_long = gb.melt(
#       id_vars=["question_user_country_code", segmentation, time],
#       value_vars=gb.columns[2:],
#       var_name="category",
#       value_name="pct"
#     )

#     gb_long["segment_color"] = gb_long[segmentation].map(segment_colors_dct)

#     gb_country_segment_b_topic_time_dct[segmentation][time] = gb_long

In [33]:
gb_country_segment_b_topic_time_dct["speed_post_response"]["question_set_dt_year"]

question_user_country_code speed_post_response  question_set_dt_year  \
0                           KE                   1                  2017   
35                          UG                   2                  2017   
45                          UG                   4                  2017   
40                          UG                   3                  2017   
55                          KE                   1                  2017   
50                          UG                   5                  2017   
325                         UG                   5                  2017   
61                          KE                   2                  2017   
330                         KE                   1                  2017   
336                         KE                   2                  2017   
342                         KE                   3                  2017   
85                          UG                   1                  2017   
79                          KE                   5                  2017   
73                          KE                   4                  2017   
67                          KE                   3                  2017   
348                         KE                   4                  2017   
90                          UG                   2                  2017   
95                          UG                   3                  2017   
293                         KE                   4                  2017   
299                         KE                   5                  2017   
305                         UG                   1                  2017   
310                         UG                   2                  2017   
265                         UG                   4                  2017   
260                         UG                   3                  2017   
116                         KE                   2                  2017   
122                         KE                   3                  2017   
128                         KE                   4                  2017   
110                         KE                   1                  2017   
105                         UG                   5                  2017   
100                         UG                   4                  2017   
320                         UG                   4                  2017   
315                         UG                   3                  2017   
275                         KE                   1                  2017   
281                         KE                   2                  2017   
287                         KE                   3                  2017   
134                         KE                   5                  2017   
140                         UG                   1                  2017   
270                         UG                   5                  2017   
150                         UG                   3                  2017   
145                         UG                   2                  2017   
226                         KE                   2                  2017   
155                         UG                   4                  2017   
232                         KE                   3                  2017   
160                         UG                   5                  2017   
24                          KE                   5                  2017   
30                          UG                   1                  2017   
12                          KE                   3                  2017   
6                           KE                   2                  2017   
200                         UG                   2                  2017   
205                         UG                   3                  2017   
210                         UG                   4                  2017   
215                         UG                   5  

In [44]:
gb_country_segment_n_topic_time_dct = defaultdict(dict)
for segmentation in segmentation_collst:
  for time in time_collst:
    gb_sum = all3.groupby([
      "question_user_country_code",
      segmentation,
      time
    ])[niche_collst].sum()

    gb_count = all3.groupby([
      "question_user_country_code",
      segmentation,
      time
    ]).size()

    row_sums = gb_sum[niche_collst].sum(axis=1)
    gb_pct = gb_sum[niche_collst].div(row_sums, axis=0)
    gb_se = np.sqrt(gb_pct * (1 - gb_pct)).div(np.sqrt(gb_count), axis=0)

    gb_pct = gb_pct.reset_index()
    gb_se = gb_se.reset_index()
    gb_sum = gb_sum.reset_index()
    gb_sum['count'] = gb_count.values

    gb_pct_long = gb_pct.melt(
      id_vars=["question_user_country_code", segmentation, time],
      value_vars=niche_collst,
      var_name="category",
      value_name="pct"
    )

    gb_se_long = gb_se.melt(
      id_vars=["question_user_country_code", segmentation, time],
      value_vars=niche_collst,
      var_name="category",
      value_name="se"
    )

    gb_long = gb_pct_long.merge(
      gb_se_long,
      on=["question_user_country_code", segmentation, time, "category"]
    ).merge(
      gb_sum[["question_user_country_code", segmentation, time, "count"]],
      on=["question_user_country_code", segmentation, time]
    ).sort_values(
      by=time,
      ascending=True
    )

    gb_long["broad_type"] = gb_long["category"].str.split("_").str[0]
    gb_long["niche"] = gb_long["category"].str.split("_").str[1]

    gb_long["segment_color"] = gb_long[segmentation].map(segment_colors_dct)

    gb_country_segment_n_topic_time_dct[segmentation][time] = gb_long

In [45]:
gb_country_segment_n_topic_time_dct["speed_post_response"]["question_set_dt_year"]

question_user_country_code speed_post_response  question_set_dt_year  \
6485                         UG                   5                  2017   
6490                         KE                   1                  2017   
6496                         KE                   2                  2017   
3575                         KE                   1                  2017   
3581                         KE                   2                  2017   
3587                         KE                   3                  2017   
12                           KE                   3                  2017   
18                           KE                   4                  2017   
5490                         UG                   4                  2017   
45                           UG                   4                  2017   
50                           UG                   5                  2017   
55                           KE                   1                  2017   
61                           KE                   2                  2017   
67                           KE                   3                  2017   
6475                         UG                   3                  2017   
6480                         UG                   4                  2017   
5540                         UG                   3                  2017   
1228                         KE                   4                  2017   
1234                         KE                   5                  2017   
1240                         UG                   1                  2017   
1245                         UG                   2                  2017   
1250                         UG                   3                  2017   
1255                         UG                   4                  2017   
5485                         UG                   3                  2017   
1260                         UG                   5                  2017   
1265                         KE                   1                  2017   
1271                         KE                   2                  2017   
1277                         KE                   3                  2017   
1283                         KE                   4                  2017   
5451                         KE                   2                  2017   
5457                         KE                   3                  2017   
5535                         UG                   2                  2017   
3560                         UG                   3                  2017   
3565                         UG                   4                  2017   
3570                         UG                   5                  2017   
3495                         UG                   1                  2017   
3500                         UG                   2                  2017   
3505                         UG                   3                  2017   
3510                         UG                   4                  2017   
3515                         UG                   5                  2017   
6453                         KE                   4                  2017   
3615                         UG                   3                  2017   
3620                         UG                   4                  2017   
3532                         KE                   3                  2017   
3538                         KE                   4                  2017   
3544                         KE                   5                  2017   
3550                         UG                   1                  2017   
3555                         UG                   2                  2017   
73                           KE                   4                  2017   
79                           KE                   5                  2017   
85                           UG                   1                  2017   
9

In [36]:
# gb_country_segment_n_topic_time_dct = defaultdict(dict)
# for segmentation in segmentation_collst:
#   for time in time_collst:
#     gb = all3.groupby([
#       "question_user_country_code",
#       segmentation,
#       time
#     ])[niche_collst].sum().reset_index()

#     row_sums = gb[niche_collst].sum(axis=1)
#     gb[niche_collst] = gb[niche_collst].div(row_sums, axis=0)

#     gb_long = gb.melt(
#       id_vars=["question_user_country_code", segmentation, time],
#       value_vars=gb.columns[2:],
#       var_name="category",
#       value_name="pct"
#     )

#     gb_long["broad_type"] = gb_long["category"].str.split("_").str[0]
#     gb_long["niche"] = gb_long["category"].str.split("_").str[1]

#     gb_long["segment_color"] = gb_long[segmentation].map(segment_colors_dct)

#     gb_country_segment_n_topic_time_dct[segmentation][time] = gb_long

# export data to google drive

In [37]:
alldata_dct = {
  "tab1": vc_country.to_dict(),
  "tab2": gb_segments_dct,
  "tab3": {
    "broad": gb_country_segment_b_topic_dct,
    "niche": gb_country_segment_n_topic_dct
  },
  "tab4": {
    "broad": gb_country_segment_b_topic_time_dct,
    "niche": gb_country_segment_n_topic_time_dct
  }
}

In [38]:
import pickle

with open("all_dashboard_data.pkl", "wb") as w:
  pickle.dump(alldata_dct, w)
!cp all_dashboard_data.pkl /content/drive/MyDrive/DataKit_WeFarm/Dashboard

In [39]:
!ls /content/drive/MyDrive/DataKit_WeFarm/Dashboard

all_dashboard_data.pkl	intersections
